In [ ]:
from model import *
from similarity import *
import csv

In [ ]:
def create_similarity_matrix(filename, key):
    with open(filename) as file:
        similarity_matrix = {}

        for line in csv.DictReader(file, skipinitialspace=True):
            for k, v in line.items():
                if k == key:
                    key_v = v
                    similarity_matrix[key_v] = {}
                else:
                    similarity_matrix[key_v][k] = float(v)

        return similarity_matrix

In [ ]:
case_base = CaseBase.from_csv(
    "data/SIM_001.csv",
    problem_fields = ("v", "v_left", "v_front", "d_left", "d_front", "type_left", "type_front", "radius_curve(m)", "slope_street", "street_type", "time", "weather", "type_vehicle", "speed_limit(km/h)"),
    solution_fields = ("action"),
    encoding = "utf-8",
    delimiter = ";",
    set_int = True
)
print(case_base)
case_base[:3]

In [ ]:
case_base.add_symbolic_sim(
    field = "type_left",
    similarity_matrix = create_similarity_matrix("data/vehicle_type_sim.csv", "type_vehicle")
)

case_base.add_symbolic_sim(
    field = "type_front",
    similarity_matrix = create_similarity_matrix("data/vehicle_type_sim.csv", "type_vehicle")
)

case_base.add_symbolic_sim(
    field = "type_vehicle",
    similarity_matrix = create_similarity_matrix("data/vehicle_type_sim.csv", "type_vehicle")
)

case_base.add_symbolic_sim(
    field = "slope_street",
    similarity_matrix = create_similarity_matrix("data/street_slope_sim.csv", "type_street_slope")
)

case_base.add_symbolic_sim(
    field = "street_type",
    similarity_matrix = create_similarity_matrix("data/street_type_sim.csv", "type_street")
)

case_base.add_symbolic_sim(
    field = "time",
    similarity_matrix = create_similarity_matrix("data/time_type_sim.csv", "type_time")
)

case_base.add_symbolic_sim(
    field = "weather",
    similarity_matrix = create_similarity_matrix("data/weather_type_sim.csv", "type_weather")
)


In [ ]:
query = Query.from_problems(
    v = 28.5,
    v_left = 42.5,
    v_front = 5,
    d_left = -137,
    d_front = 54,
    type_left = "motorcycle",
    type_front = "truck",
    radius_curve = 2391,
    slope_street = "flat",
    street_type = "country_road (separated)",
    time = "day",
    weather = "dry",
    type_vehicle = "car",
    speed_limit = 100,
)

# sim_funcs: manhattan_sim, euclid_sim
retrieved = case_base.retrieve(
    query,
    v_left = euclid_sim,
    v_front = euclid_sim,
    d_left = euclid_sim,
    d_front = euclid_sim,
    type_left = symbolic_sim,
    type_front = symbolic_sim,
    radius_curve = euclid_sim,
    slope_street = symbolic_sim,
    street_type = symbolic_sim,
    time = symbolic_sim,
    weather = symbolic_sim,
    type_vehicle = symbolic_sim,
    speed_limit = euclid_sim,
)

print("Your Query:")
for k, v in query.problem.items():
    print(f"  - {k} = {v}")
print()
print("I recommend you this car:")
print(" ".join(retrieved.solution.values()).capitalize())
print()
print("Explanation:")
for field, sim_val in retrieved.sim_per_field.items():
    print(f"  - {field} =", retrieved.problem[field], f"(similarity: {sim_val:.2f})")